# Introduction

In [1]:
import geopandas as gpd
import folium
from folium import plugins
import json
import geojson

## Folium - The Mapping Tool 

### Create Map

In [2]:
# use buzzfeed lat/lon
buzzfeed_coords = [44.998981, -93.246634]
map_ = folium.Map(location=buzzfeed_coords, zoom_start=12)
map_

In [3]:
folium.Marker(location = buzzfeed_coords, popup="BuzzFeed", icon=folium.Icon(icon='cloud')).add_to(map_)
map_

### Geopandas - the data tool 

__[Minneapolis Pedestrian and Bicycle Trails Open Dataset](http://opendata.minneapolismn.gov/datasets/8d110c659d614474839c9c0642d8974a_0)__


In [4]:
# read in file using geopandas
trails = gpd.read_file(r"C:\Users\murra667\Documents\Springboard\Geopandas Presentation\Pedestrian_and_Bicycle_Trails\Pedestrian_and_Bicycle_Trails.shp")

In [5]:
# defining the projection 
trails = trails.to_crs({'init': 'epsg:4326'})

In [6]:
trails.head()

FID  ID                     TRAIL_NAME               BYWAY_DIST  \
0    1   0  North Hennepin Regional Trail   Victory Memorial Byway   
1    2   0             Grand Rounds Trail  Mississippi River Byway   
2    3   0  North Hennepin Regional Trail   Victory Memorial Byway   
3    4   0                  Kenwood Trail     Theodore Wirth Byway   
4    5   0  North Hennepin Regional Trail   Victory Memorial Byway   

            PKWY_NAME        LENGTH  SHAPE_LEN  \
0  Shingle Creek Pkwy   1695.845600          0   
1        Hiawatha Ave  12906.101440          0   
2  Shingle Creek Pkwy    187.352599          0   
3        Kenwood Pkwy   5078.112933          0   
4  Shingle Creek Pkwy   1132.261383          0   

                                            geometry  
0  LINESTRING (-93.2956742816568 45.0360316630074...  
1  LINESTRING (-93.2410408235131 44.9516543156037...  
2  LINESTRING (-93.2967850361086 45.0383465610618...  
3  LINESTRING (-93.305486855458 44.9692653553163,...  
4  LINESTRING (-93.2962792266016 45.0385117539769...

### Geopandas and Folium - a great mix!

In [7]:
folium.GeoJson(trails,
    style_function=lambda feature: {
        'fillColor': 'red',
        'color' : 'red',
        'weight' : 1,
        'fillOpacity' : 0.5,
        }
    ).add_to(map_).add_to(map_)
map_

In [8]:
del map_

### Bringing In The Data

__[Minneapolis Neighborhoods GIS Open Dataset](http://opendata.minneapolismn.gov/datasets/neighborhoods)__

__[Minneapolis Parks GIS Open Dataset](http://opendata.minneapolismn.gov/datasets/a1847c4cc69940f99b46b16e2b4fe7e3_0)__


#### Read in Data

In [9]:
# read parks shapefile
parks = gpd.read_file(r"C:\Users\murra667\Documents\Springboard\Geopandas Presentation\Parks\Parks.shp")
# read in neighborhoods shapefile
hoods = gpd.read_file(r"C:\Users\murra667\Documents\Springboard\Geopandas Presentation\Neighborhoods\Neighborhoods.shp")


In [10]:
map_ = folium.Map(location=buzzfeed_coords, zoom_start=12)
folium.GeoJson(hoods,
    style_function=lambda feature: {
        'fill color' : 'None',
        'color' : 'red',
        'weight' : 1,
        'fillOpacity' : 0.0,
        }
    ).add_to(map_).add_to(map_)
map_

In [11]:
folium.GeoJson(parks,
    style_function=lambda feature: {
        'fillColor': 'red',
        'color' : 'red',
        'weight' : 1,
        'fillOpacity' : 0.5,
        }
    ).add_to(map_).add_to(map_)
map_

#### Assign Projections

In [12]:
# assign coordinate system projection of both files 
parks = parks.to_crs({'init': 'epsg:4326'})
hoods = hoods.to_crs({'init': 'epsg:4326'})

#### Quick Clean

In [13]:
# rename parks column
hoods = hoods.rename(columns = {'BDNAME' : 'hood'})

### Joining Data Spatially

In [14]:
# spatially join parks to 
parks_in_hoods = gpd.sjoin(parks, hoods, op='within')
parks_in_hoods.head()

FID  OBJECTID_left INT_REFNO_left PREFIX_left UDI_left SYMBOL_NAM_left  \
0     1             28    -2150000000       REFNO  1195.27        PARKAREA   
1     2             29    -2150000000       REFNO  1195.28        PARKAREA   
15   16             43    -2150000000       REFNO  1195.50        PARKAREA   
56   57             27    -2150000000       REFNO  1195.26        PARKAREA   
2     3             31    -2150000000       REFNO  1195.35        PARKAREA   

      REFNO   PARENT  SYMBOL_NUM  WID     ...      OBJECTID_right  \
0   1195.27  PBSHADE         424   38     ...                  20   
1   1195.28  PBSHADE         424   39     ...                  20   
15  1195.50  PBSHADE         424   53     ...                  20   
56  1195.26  PBSHADE         424   37     ...                  20   
2   1195.35  PBSHADE         424   41     ...                  73   

    INT_REFNO_right PREFIX_right UDI_right SYMBOL_NAM_right           hood  \
0       -2144137400        REFNO  23126.00         WARDAREA  Willard - Hay   
1       -2144137400        REFNO  23126.00         WARDAREA  Willard - Hay   
15      -2144137400        REFNO  23126.00         WARDAREA  Willard - Hay   
56      -2144137400        REFNO  23126.00         WARDAREA  Willard - Hay   
2       -2144133000        REFNO  23170.00         WARDAREA   East Harriet   

    BDNUM  TEXT_NBR Shape__Are  Shape__Len  
0      26        26   0.000313    0.088445  
1      26        26   0.000313    0.088445  
15     26        26   0.000313    0.088445  
56     26        26   0.000313    0.088445  
2      70        70   0.000367    0.079085  

[5 rows x 34 columns]

### Sum Acreage in Parks Per Neighborhood

In [15]:
count_parks = parks_in_hoods.groupby('hood')['ACRES'].sum().reset_index (name = "ACRES")
count_parks.head()

hood      ACRES
0      Armatage  18.999743
1  Audubon Park   5.709848
2      Beltrami   8.107783
3     Bottineau  12.191639
4        Bryant   7.816835

### Rejoin Counted Parks With Neighborhood Boundaries Spatial Data 

In [16]:
# rejoin counted parks with parks shapefile
parks_hoods_count = count_parks.merge(hoods, how = "outer", left_on = "hood", right_on = "hood")
parks_hoods_count = gpd.GeoDataFrame(parks_hoods_count)
parks_hoods_count.head()

hood      ACRES  OBJECTID   INT_REFNO PREFIX       UDI SYMBOL_NAM  \
0      Armatage  18.999743        60 -2144133400  REFNO  23166.00   WARDAREA   
1  Audubon Park   5.709848        49 -2144138400  REFNO  23116.00   WARDAREA   
2      Beltrami   8.107783        61 -2144137700  REFNO  23123.00   WARDAREA   
3     Bottineau  12.191639        31 -2144138600  REFNO  23114.00   WARDAREA   
4        Bryant   7.816835        58 -2144134300  REFNO  23157.00   WARDAREA   

  BDNUM TEXT_NBR  Shape__Are  Shape__Len  \
0    66       66    0.000218    0.058679   
1    16       16    0.000197    0.061454   
2    23       23    0.000067    0.035456   
3    14       14    0.000084    0.038396   
4    57       57    0.000088    0.038802   

                                            geometry  
0  POLYGON ((-93.3175183363998 44.9052091627858, ...  
1  POLYGON ((-93.2426719609751 45.0239333964277, ...  
2  POLYGON ((-93.23786766213949 44.9932847686681,...  
3  POLYGON ((-93.26309004305401 45.0052745826247,...  
4  POLYGON ((-93.2625117382169 44.9269406537315, ...

### Creating Geojson To Use With Folium

In [17]:
parks_hoods_choropleth_json = parks_hoods_count.to_json()

### Create Choropleth Map

__[Color Brewer As Fill Color Parameter](http://colorbrewer2.org/#type=sequential&scheme=Greens&n=3)__

In [18]:
parks_map = folium.Map(location=[44.986656, -93.258133], zoom_start=12)
# create choropleth map
parks_map.choropleth(geo_data = parks_hoods_choropleth_json, data = parks_hoods_count,
         columns=['hood', 'ACRES'],
         key_on='feature.properties.hood',
         #threshold_scale = [-.05, -.025, -.005, .005, .025, .05],
         legend_name = 'Number of Parks in Minneapolis Neighborhoods', fill_opacity=.8, line_opacity=.9,
         fill_color='Greens' )
parks_map

### Add Trails Layer and Save Out As Html

In [19]:
folium.GeoJson(trails,
    style_function=lambda feature: {
        'fillColor': 'red',
        'color' : 'red',
        'weight' : 1,
        'fillOpacity' : 0.5,
        }
    ).add_to(parks_map).add_to(parks_map)
parks_map.save('parks_map.html')

other good resources 
https://www.kaggle.com/daveianhickey/how-to-folium-for-maps-heatmaps-time-analysis

In [ ]:
murra667@umn.edu